In [1]:
# PRE-REQUISITE CONNECTION 

from pymongo import MongoClient

client = MongoClient("mongodb://localhost:27017/")
try:
    server_info = client.server_info()
    print("Connected to MongoDB Server")
except Exception as e:
    print("Error connecting to MongoDB:", e)

databases = client.list_database_names()
print("Databases:", databases)

Connected to MongoDB Server
Databases: ['admin', 'config', 'durham_data', 'local', 'meteorites_db', 'restaurants_db', 'worldcities_db']


# Question 0 is at the Last 

In [2]:
# UTILITY CODE TO DELETE THE COLLECTIONS, PLEASE USE THIS TO DELETE ALL COLLECTIONS, BEFORE RE-RUNNING THE NOTEBOOK! 
# I AM PLACING THIS AT THE BEGINNING SO THAT FOR EACH RUN, WELL START AFRESH. 

for db_name in databases:
    if db_name in ['admin', 'config', 'local']:
        continue
    db = client[db_name]
    
    collections = db.list_collection_names()
    for collection_name in collections:
        print(f"Deleting collection: {collection_name} from database: {db_name}")
        db.drop_collection(collection_name)

print("All collections and databases (if specified) have been deleted.")

Deleting collection: durham_foreclosures from database: durham_data
Deleting collection: durham_restaurants from database: durham_data
Deleting collection: meteorites from database: meteorites_db
Deleting collection: restaurants from database: restaurants_db
Deleting collection: cities from database: worldcities_db
All collections and databases (if specified) have been deleted.


In [3]:
import pymongo
import pandas as pd
import json
from datetime import datetime

with open('restaurants.json', 'r') as file:
    restaurants_data = json.load(file)

df = pd.DataFrame(restaurants_data)

def convert_to_iso(grades):
    for grade in grades:
        if 'date' in grade:
            timestamp = grade['date']['$date'] / 1000
            grade['date'] = datetime.utcfromtimestamp(timestamp).isoformat()
    return grades

df['grades'] = df['grades'].apply(convert_to_iso)

client = pymongo.MongoClient("mongodb://localhost:27017/")
db = client["restaurants_db"]
collection = db["restaurants"]
data_to_insert = df.to_dict(orient="records")

# Insert data into MongoDB
collection.insert_many(data_to_insert)

print("Data inserted successfully.")

for doc in collection.find().limit(5): 
    print(doc)


/Users/sainishanth/anaconda3/lib/python3.10/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


Data inserted successfully.
{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-09-11T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2013-01-24T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2011-11-23T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2011-03-10T00:00:00', 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'_id': ObjectId('6749593179a7fce314ff1bb5'), 'address': {'building': '469', 'coord': [-73.961704, 40.662942], 'street': 'Flatbush Avenue', 'zipcode': '11225'}, 'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'grades': [{'date': '2014-12-30T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2014-07-01T00:00:00', 'grade': 'B', 'score': 23}, {'date': '2013-04-30T00:00:00', 'grade': 'A', 'score': 12},

# QUESTION 1 : Write MongoDB queries for (2 points each):

In [4]:
# 1. COUNT THE NUMBER OF DOCUMENTS IN THE COLLECTION 

print("Total documents:", collection.count_documents({}))

Total documents: 3772


In [5]:
# 2. DISPLAY ALL THE DOCUMENTS IN THE COLLECTIONS
for doc in collection.find():
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-09-11T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2013-01-24T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2011-11-23T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2011-03-10T00:00:00', 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'_id': ObjectId('6749593179a7fce314ff1bb5'), 'address': {'building': '469', 'coord': [-73.961704, 40.662942], 'street': 'Flatbush Avenue', 'zipcode': '11225'}, 'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'grades': [{'date': '2014-12-30T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2014-07-01T00:00:00', 'grade': 'B', 'score': 23}, {'date': '2013-04-30T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2012-05-08T00:00:

In [6]:
# 3. Display restaurant_id, name, borough, and cuisine for all the documents
for doc in collection.find({}, {"restaurant_id": 1, "name": 1, "borough": 1, "cuisine": 1, "_id": 0}):
    print(doc)


{'borough': 'Bronx', 'cuisine': 'Bakery', 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'name': "Wendy'S", 'restaurant_id': '30112340'}
{'borough': 'Manhattan', 'cuisine': 'Irish', 'name': 'Dj Reynolds Pub And Restaurant', 'restaurant_id': '30191841'}
{'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Riviera Caterer', 'restaurant_id': '40356018'}
{'borough': 'Queens', 'cuisine': 'Jewish/Kosher', 'name': 'Tov Kosher Kitchen', 'restaurant_id': '40356068'}
{'borough': 'Queens', 'cuisine': 'American ', 'name': 'Brunos On The Boulevard', 'restaurant_id': '40356151'}
{'borough': 'Staten Island', 'cuisine': 'Jewish/Kosher', 'name': 'Kosher Island', 'restaurant_id': '40356442'}
{'borough': 'Brooklyn', 'cuisine': 'Delicatessen', 'name': "Wilken'S Fine Food", 'restaurant_id': '40356483'}
{'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Regina Caterers', 'restaurant_id': '40356649'}
{'borough': 'Brooklyn', 'cuisine': 

In [7]:
# 4. Display restaurant_id, name, borough, and cuisine, but exclude _id for all documents

for doc in collection.find({}, {"restaurant_id": 1, "name": 1, "borough": 1, "cuisine": 1, "_id": 0}):
    print(doc)

{'borough': 'Bronx', 'cuisine': 'Bakery', 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'name': "Wendy'S", 'restaurant_id': '30112340'}
{'borough': 'Manhattan', 'cuisine': 'Irish', 'name': 'Dj Reynolds Pub And Restaurant', 'restaurant_id': '30191841'}
{'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Riviera Caterer', 'restaurant_id': '40356018'}
{'borough': 'Queens', 'cuisine': 'Jewish/Kosher', 'name': 'Tov Kosher Kitchen', 'restaurant_id': '40356068'}
{'borough': 'Queens', 'cuisine': 'American ', 'name': 'Brunos On The Boulevard', 'restaurant_id': '40356151'}
{'borough': 'Staten Island', 'cuisine': 'Jewish/Kosher', 'name': 'Kosher Island', 'restaurant_id': '40356442'}
{'borough': 'Brooklyn', 'cuisine': 'Delicatessen', 'name': "Wilken'S Fine Food", 'restaurant_id': '40356483'}
{'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Regina Caterers', 'restaurant_id': '40356649'}
{'borough': 'Brooklyn', 'cuisine': 

In [8]:
#5. 5. Display restaurant_id, name, borough, and zipcode, excluding _id for all documents

for doc in collection.find({}, {"restaurant_id": 1, "name": 1, "borough": 1, "address.zipcode": 1, "_id": 0}):
    print(doc)


{'address': {'zipcode': '10462'}, 'borough': 'Bronx', 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'address': {'zipcode': '11225'}, 'borough': 'Brooklyn', 'name': "Wendy'S", 'restaurant_id': '30112340'}
{'address': {'zipcode': '10019'}, 'borough': 'Manhattan', 'name': 'Dj Reynolds Pub And Restaurant', 'restaurant_id': '30191841'}
{'address': {'zipcode': '11224'}, 'borough': 'Brooklyn', 'name': 'Riviera Caterer', 'restaurant_id': '40356018'}
{'address': {'zipcode': '11374'}, 'borough': 'Queens', 'name': 'Tov Kosher Kitchen', 'restaurant_id': '40356068'}
{'address': {'zipcode': '11369'}, 'borough': 'Queens', 'name': 'Brunos On The Boulevard', 'restaurant_id': '40356151'}
{'address': {'zipcode': '10314'}, 'borough': 'Staten Island', 'name': 'Kosher Island', 'restaurant_id': '40356442'}
{'address': {'zipcode': '11234'}, 'borough': 'Brooklyn', 'name': "Wilken'S Fine Food", 'restaurant_id': '40356483'}
{'address': {'zipcode': '11219'}, 'borough': 'Brooklyn', 'name': 'Regina

In [9]:
#6. Display all the restaurants in the Bronx

for doc in collection.find({"borough": "Bronx"}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-09-11T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2013-01-24T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2011-11-23T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2011-03-10T00:00:00', 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'_id': ObjectId('6749593179a7fce314ff1bbe'), 'address': {'building': '2300', 'coord': [-73.8786113, 40.8502883], 'street': 'Southern Boulevard', 'zipcode': '10460'}, 'borough': 'Bronx', 'cuisine': 'American ', 'grades': [{'date': '2014-05-28T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-06-19T00:00:00', 'grade': 'A', 'score': 4}, {'date': '2012-06-15T00:00:00', 'grade': 'A', 'score': 3}], 'name': 'Wild Asia', 'res

In [10]:
#7 7. Display the first 5 restaurants in the Bronx

for doc in collection.find({"borough": "Bronx"}).limit(5):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-09-11T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2013-01-24T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2011-11-23T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2011-03-10T00:00:00', 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'_id': ObjectId('6749593179a7fce314ff1bbe'), 'address': {'building': '2300', 'coord': [-73.8786113, 40.8502883], 'street': 'Southern Boulevard', 'zipcode': '10460'}, 'borough': 'Bronx', 'cuisine': 'American ', 'grades': [{'date': '2014-05-28T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-06-19T00:00:00', 'grade': 'A', 'score': 4}, {'date': '2012-06-15T00:00:00', 'grade': 'A', 'score': 3}], 'name': 'Wild Asia', 'res

In [11]:
# 8. Display the second 5 restaurants (skipping the first 5) in the Bronx

for doc in collection.find({"borough": "Bronx"}).skip(5).limit(5):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bf1'), 'address': {'building': '658', 'coord': [-73.81363999999999, 40.82941100000001], 'street': 'Clarence Ave', 'zipcode': '10465'}, 'borough': 'Bronx', 'cuisine': 'American ', 'grades': [{'date': '2014-06-21T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2012-07-11T00:00:00', 'grade': 'A', 'score': 10}], 'name': 'Manhem Club', 'restaurant_id': '40364363'}
{'_id': ObjectId('6749593179a7fce314ff1c09'), 'address': {'building': '2222', 'coord': [-73.84971759999999, 40.8304811], 'street': 'Haviland Avenue', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'American ', 'grades': [{'date': '2014-12-18T00:00:00', 'grade': 'A', 'score': 7}, {'date': '2014-05-01T00:00:00', 'grade': 'B', 'score': 17}, {'date': '2013-03-14T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2012-09-20T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2012-02-08T00:00:00', 'grade': 'B', 'score': 19}], 'name': 'The New Starling Athletic Club Of The Bronx', 'restaurant_id': '4

In [12]:
# 9. Find the restaurants with any score more than 85

for doc in collection.find({"grades.score": {"$gt": 85}}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1d12'), 'address': {'building': '65', 'coord': [-73.9782725, 40.7624022], 'street': 'West   54 Street', 'zipcode': '10019'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-08-22T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2014-03-28T00:00:00', 'grade': 'C', 'score': 131}, {'date': '2013-09-25T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-04-08T00:00:00', 'grade': 'B', 'score': 25}, {'date': '2012-10-15T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2011-10-19T00:00:00', 'grade': 'A', 'score': 13}], 'name': "Murals On 54/Randolphs'S", 'restaurant_id': '40372466'}
{'_id': ObjectId('6749593179a7fce314ff1db3'), 'address': {'building': '345', 'coord': [-73.9864626, 40.7266739], 'street': 'East 6 Street', 'zipcode': '10003'}, 'borough': 'Manhattan', 'cuisine': 'Indian', 'grades': [{'date': '2014-09-15T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2014-01-14T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-0

In [13]:
# 10. Find the restaurants that achieved a score more than 80 but less than 100
for doc in collection.find({"grades.score": {"$gt": 80, "$lt": 100}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1d12'), 'address': {'building': '65', 'coord': [-73.9782725, 40.7624022], 'street': 'West   54 Street', 'zipcode': '10019'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-08-22T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2014-03-28T00:00:00', 'grade': 'C', 'score': 131}, {'date': '2013-09-25T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-04-08T00:00:00', 'grade': 'B', 'score': 25}, {'date': '2012-10-15T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2011-10-19T00:00:00', 'grade': 'A', 'score': 13}], 'name': "Murals On 54/Randolphs'S", 'restaurant_id': '40372466'}
{'_id': ObjectId('6749593179a7fce314ff1db3'), 'address': {'building': '345', 'coord': [-73.9864626, 40.7266739], 'street': 'East 6 Street', 'zipcode': '10003'}, 'borough': 'Manhattan', 'cuisine': 'Indian', 'grades': [{'date': '2014-09-15T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2014-01-14T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-0

In [14]:
# 11. Find the restaurants which locate in longitude value less than -95.754168

for doc in collection.find({"address.coord.0": {"$lt": -95.754168}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff21fc'), 'address': {'building': '3707', 'coord': [-101.8945214, 33.5197474], 'street': '82 Street', 'zipcode': '11372'}, 'borough': 'Queens', 'cuisine': 'American ', 'grades': [{'date': '2014-06-04T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-11-07T00:00:00', 'grade': 'B', 'score': 19}, {'date': '2013-05-17T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-08-29T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-04-03T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2011-11-16T00:00:00', 'grade': 'A', 'score': 7}], 'name': 'Burger King', 'restaurant_id': '40534067'}
{'_id': ObjectId('6749593179a7fce314ff2567'), 'address': {'building': '15259', 'coord': [-119.6368672, 36.2504996], 'street': '10 Avenue', 'zipcode': '11357'}, 'borough': 'Queens', 'cuisine': 'Italian', 'grades': [{'date': '2014-09-04T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2014-03-26T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-03-04T00:00:00', 'grade':

In [15]:
# 12. Find restaurants that do not prepare any cuisine of "American" and their grade score > 70 and longitude < -65.754168

for doc in collection.find({
    "cuisine": {"$ne": "American"},
    "grades.score": {"$gt": 70},
    "address.coord.0": {"$lt": -65.754168}
}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1d12'), 'address': {'building': '65', 'coord': [-73.9782725, 40.7624022], 'street': 'West   54 Street', 'zipcode': '10019'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-08-22T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2014-03-28T00:00:00', 'grade': 'C', 'score': 131}, {'date': '2013-09-25T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-04-08T00:00:00', 'grade': 'B', 'score': 25}, {'date': '2012-10-15T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2011-10-19T00:00:00', 'grade': 'A', 'score': 13}], 'name': "Murals On 54/Randolphs'S", 'restaurant_id': '40372466'}
{'_id': ObjectId('6749593179a7fce314ff1db3'), 'address': {'building': '345', 'coord': [-73.9864626, 40.7266739], 'street': 'East 6 Street', 'zipcode': '10003'}, 'borough': 'Manhattan', 'cuisine': 'Indian', 'grades': [{'date': '2014-09-15T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2014-01-14T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-0

In [16]:
# 13. Without using $and operator

for doc in collection.find({
    "cuisine": {"$ne": "American"},
    "grades.score": {"$gt": 70},
    "address.coord.0": {"$lt": -65.754168}
}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1d12'), 'address': {'building': '65', 'coord': [-73.9782725, 40.7624022], 'street': 'West   54 Street', 'zipcode': '10019'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-08-22T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2014-03-28T00:00:00', 'grade': 'C', 'score': 131}, {'date': '2013-09-25T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-04-08T00:00:00', 'grade': 'B', 'score': 25}, {'date': '2012-10-15T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2011-10-19T00:00:00', 'grade': 'A', 'score': 13}], 'name': "Murals On 54/Randolphs'S", 'restaurant_id': '40372466'}
{'_id': ObjectId('6749593179a7fce314ff1db3'), 'address': {'building': '345', 'coord': [-73.9864626, 40.7266739], 'street': 'East 6 Street', 'zipcode': '10003'}, 'borough': 'Manhattan', 'cuisine': 'Indian', 'grades': [{'date': '2014-09-15T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2014-01-14T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-0

In [17]:
# 14. Restaurants not preparing "American," scored grade "A," not in Brooklyn, sorted by cuisine descending

for doc in collection.find({
    "cuisine": {"$ne": "American"},
    "grades.grade": "A",
    "borough": {"$ne": "Brooklyn"}
}).sort("cuisine", -1):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff22c0'), 'address': {'building': '89', 'coord': [-73.9995899, 40.7168015], 'street': 'Baxter Street', 'zipcode': '10013'}, 'borough': 'Manhattan', 'cuisine': 'Vietnamese/Cambodian/Malaysia', 'grades': [{'date': '2014-08-21T00:00:00', 'grade': 'A', 'score': 13}, {'date': '2013-08-31T00:00:00', 'grade': 'A', 'score': 13}, {'date': '2013-04-11T00:00:00', 'grade': 'C', 'score': 3}, {'date': '2012-10-17T00:00:00', 'grade': 'A', 'score': 4}, {'date': '2012-05-15T00:00:00', 'grade': 'A', 'score': 10}], 'name': 'Thai Son', 'restaurant_id': '40559606'}
{'_id': ObjectId('6749593179a7fce314ff2379'), 'address': {'building': '8278', 'coord': [-73.88143509999999, 40.7412552], 'street': 'Broadway', 'zipcode': '11373'}, 'borough': 'Queens', 'cuisine': 'Vietnamese/Cambodian/Malaysia', 'grades': [{'date': '2014-06-12T00:00:00', 'grade': 'B', 'score': 21}, {'date': '2013-05-20T00:00:00', 'grade': 'A', 'score': 13}, {'date': '2012-12-26T00:00:00', 'grade': 'A', 'score'

In [18]:
# 15. Restaurants with "Wil" as the first three letters of the name

for doc in collection.find({"name": {"$regex": "^Wil"}}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1bbb'), 'address': {'building': '7114', 'coord': [-73.9068506, 40.6199034], 'street': 'Avenue U', 'zipcode': '11234'}, 'borough': 'Brooklyn', 'cuisine': 'Delicatessen', 'grades': [{'date': '2014-05-29T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2014-01-14T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2013-08-03T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2012-07-18T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2012-03-09T00:00:00', 'grade': 'A', 'score': 13}, {'date': '2011-10-14T00:00:00', 'grade': 'A', 'score': 9}], 'name': "Wilken'S Fine Food", 'restaurant_id': '40356483'}
{'_id': ObjectId('6749593179a7fce314ff1bbe'), 'address': {'building': '2300', 'coord': [-73.8786113, 40.8502883], 'street': 'Southern Boulevard', 'zipcode': '10460'}, 'borough': 'Bronx', 'cuisine': 'American ', 'grades': [{'date': '2014-05-28T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-06-19T00:00:00', 'grade': 'A', 'score': 4}, {'date': '2012-06-15T00

In [19]:
# 16. Restaurants with "ces" as the last three letters of the name

for doc in collection.find({"name": {"$regex": "ces$"}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff2047'), 'address': {'building': '8', 'coord': [-74.000085, 40.733807], 'street': 'Christopher Street', 'zipcode': '10014'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-12-22T00:00:00', 'grade': 'A', 'score': 7}, {'date': '2014-05-12T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2013-03-06T00:00:00', 'grade': 'A', 'score': 7}, {'date': '2012-02-22T00:00:00', 'grade': 'A', 'score': 4}], 'name': 'Pieces', 'restaurant_id': '40399910'}
{'_id': ObjectId('6749593179a7fce314ff2106'), 'address': {'building': '4605', 'coord': [-73.922226, 40.7276291], 'street': '56 Road', 'zipcode': '11378'}, 'borough': 'Queens', 'cuisine': 'American ', 'grades': [{'date': '2014-05-21T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2013-12-12T00:00:00', 'grade': 'A', 'score': 7}, {'date': '2012-11-20T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2011-12-05T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2011-05-25T00:00:00', 'grade': 'A', 

In [20]:
# 17. Restaurants with "Reg" as three letters somewhere in the name

# 'REG' anywhere
for doc in collection.find({"name": {"$regex": "Reg"}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bbc'), 'address': {'building': '6409', 'coord': [-74.00528899999999, 40.628886], 'street': '11 Avenue', 'zipcode': '11219'}, 'borough': 'Brooklyn', 'cuisine': 'American ', 'grades': [{'date': '2014-07-18T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-07-30T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-02-13T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-08-16T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2011-08-17T00:00:00', 'grade': 'A', 'score': 11}], 'name': 'Regina Caterers', 'restaurant_id': '40356649'}
{'_id': ObjectId('6749593179a7fce314ff1cb9'), 'address': {'building': '119', 'coord': [-74.00041689999999, 40.7302678], 'street': 'Mac Dougal Street', 'zipcode': '10012'}, 'borough': 'Manhattan', 'cuisine': 'Café/Coffee/Tea', 'grades': [{'date': '2015-01-08T00:00:00', 'grade': 'A', 'score': 7}, {'date': '2014-07-22T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-08-14T00:00:00', 'grade': 'A', 'score': 12}, {'date

In [21]:
# 'R, E, G' anywhere

for doc in collection.find({"name": {"$regex": "(?=.*R)(?=.*e)(?=.*g)"}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bbc'), 'address': {'building': '6409', 'coord': [-74.00528899999999, 40.628886], 'street': '11 Avenue', 'zipcode': '11219'}, 'borough': 'Brooklyn', 'cuisine': 'American ', 'grades': [{'date': '2014-07-18T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-07-30T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-02-13T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-08-16T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2011-08-17T00:00:00', 'grade': 'A', 'score': 11}], 'name': 'Regina Caterers', 'restaurant_id': '40356649'}
{'_id': ObjectId('6749593179a7fce314ff1c26'), 'address': {'building': '181-08', 'coord': [-73.7867565, 40.7271312], 'street': 'Union Turnpike', 'zipcode': '11366'}, 'borough': 'Queens', 'cuisine': 'Chinese', 'grades': [{'date': '2014-10-22T00:00:00', 'grade': 'B', 'score': 14}, {'date': '2014-04-09T00:00:00', 'grade': 'A', 'score': 13}, {'date': '2013-07-13T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2013-01-02T00

In [22]:
# 'R, E, G' anywhere but with case-sensitive option removed.

for doc in collection.find({"name": {"$regex": "(?=.*R)(?=.*e)(?=.*g)", "$options": "i"}}):
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bbc'), 'address': {'building': '6409', 'coord': [-74.00528899999999, 40.628886], 'street': '11 Avenue', 'zipcode': '11219'}, 'borough': 'Brooklyn', 'cuisine': 'American ', 'grades': [{'date': '2014-07-18T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-07-30T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2013-02-13T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-08-16T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2011-08-17T00:00:00', 'grade': 'A', 'score': 11}], 'name': 'Regina Caterers', 'restaurant_id': '40356649'}
{'_id': ObjectId('6749593179a7fce314ff1bbf'), 'address': {'building': '7715', 'coord': [-73.9973325, 40.61174889999999], 'street': '18 Avenue', 'zipcode': '11214'}, 'borough': 'Brooklyn', 'cuisine': 'American ', 'grades': [{'date': '2014-04-16T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2013-04-23T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2012-04-24T00:00:00', 'grade': 'A', 'score': 5}, {'date': '2011-12-16T0

In [23]:
# 18. Restaurants in the Bronx serving either American or Chinese cuisine

for doc in collection.find({"borough": "Bronx", "cuisine": {"$in": ["American", "Chinese"]}}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1bd7'), 'address': {'building': '1236', 'coord': [-73.8893654, 40.81376179999999], 'street': '238 Spofford Ave', 'zipcode': '10474'}, 'borough': 'Bronx', 'cuisine': 'Chinese', 'grades': [{'date': '2013-12-30T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2013-01-08T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2012-06-12T00:00:00', 'grade': 'B', 'score': 15}], 'name': 'Happy Garden', 'restaurant_id': '40363289'}
{'_id': ObjectId('6749593179a7fce314ff1be9'), 'address': {'building': '277', 'coord': [-73.8941893, 40.8634684], 'street': 'East Kingsbridge Road', 'zipcode': '10458'}, 'borough': 'Bronx', 'cuisine': 'Chinese', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2013-09-26T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2013-03-19T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2012-08-29T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2011-08-17T00:00:00', 'grade': 'A', 'score': 13}], 'name': 'Happy Gard

In [24]:
# 19. Restaurants in Staten Island, Queens, Bronx, or Brooklyn

for doc in collection.find({"borough": {"$in": ["Staten Island", "Queens", "Bronx", "Brooklyn"]}}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'address': {'building': '1007', 'coord': [-73.856077, 40.848447], 'street': 'Morris Park Ave', 'zipcode': '10462'}, 'borough': 'Bronx', 'cuisine': 'Bakery', 'grades': [{'date': '2014-03-03T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-09-11T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2013-01-24T00:00:00', 'grade': 'A', 'score': 10}, {'date': '2011-11-23T00:00:00', 'grade': 'A', 'score': 9}, {'date': '2011-03-10T00:00:00', 'grade': 'B', 'score': 14}], 'name': 'Morris Park Bake Shop', 'restaurant_id': '30075445'}
{'_id': ObjectId('6749593179a7fce314ff1bb5'), 'address': {'building': '469', 'coord': [-73.961704, 40.662942], 'street': 'Flatbush Avenue', 'zipcode': '11225'}, 'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'grades': [{'date': '2014-12-30T00:00:00', 'grade': 'A', 'score': 8}, {'date': '2014-07-01T00:00:00', 'grade': 'B', 'score': 23}, {'date': '2013-04-30T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2012-05-08T00:00:

In [25]:
# 20. Restaurants not in Staten Island, Queens, Bronx, or Brooklyn

for doc in collection.find({"borough": {"$nin": ["Staten Island", "Queens", "Bronx", "Brooklyn"]}}):
    print(doc)


{'_id': ObjectId('6749593179a7fce314ff1bb6'), 'address': {'building': '351', 'coord': [-73.98513559999999, 40.7676919], 'street': 'West   57 Street', 'zipcode': '10019'}, 'borough': 'Manhattan', 'cuisine': 'Irish', 'grades': [{'date': '2014-09-06T00:00:00', 'grade': 'A', 'score': 2}, {'date': '2013-07-22T00:00:00', 'grade': 'A', 'score': 11}, {'date': '2012-07-31T00:00:00', 'grade': 'A', 'score': 12}, {'date': '2011-12-29T00:00:00', 'grade': 'A', 'score': 12}], 'name': 'Dj Reynolds Pub And Restaurant', 'restaurant_id': '30191841'}
{'_id': ObjectId('6749593179a7fce314ff1bc1'), 'address': {'building': '1', 'coord': [-73.96926909999999, 40.7685235], 'street': 'East   66 Street', 'zipcode': '10065'}, 'borough': 'Manhattan', 'cuisine': 'American ', 'grades': [{'date': '2014-05-07T00:00:00', 'grade': 'A', 'score': 3}, {'date': '2013-05-03T00:00:00', 'grade': 'A', 'score': 4}, {'date': '2012-04-30T00:00:00', 'grade': 'A', 'score': 6}, {'date': '2011-12-27T00:00:00', 'grade': 'A', 'score': 0}]

In [26]:
# 21. Restaurants with a score below 10

results = collection.find(
    {
        "grades.score": {"$lt": 10}  # Filter for restaurants with a score below 10
    },
    {
        "_id": 1,              # Include restaurant Id
        "name": 1,             # Include restaurant name
        "borough": 1,          # Include borough
        "cuisine": 1           # Include cuisine
    }
)

for doc in results:
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'borough': 'Bronx', 'cuisine': 'Bakery', 'name': 'Morris Park Bake Shop'}
{'_id': ObjectId('6749593179a7fce314ff1bb5'), 'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'name': "Wendy'S"}
{'_id': ObjectId('6749593179a7fce314ff1bb6'), 'borough': 'Manhattan', 'cuisine': 'Irish', 'name': 'Dj Reynolds Pub And Restaurant'}
{'_id': ObjectId('6749593179a7fce314ff1bb7'), 'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Riviera Caterer'}
{'_id': ObjectId('6749593179a7fce314ff1bb9'), 'borough': 'Queens', 'cuisine': 'American ', 'name': 'Brunos On The Boulevard'}
{'_id': ObjectId('6749593179a7fce314ff1bba'), 'borough': 'Staten Island', 'cuisine': 'Jewish/Kosher', 'name': 'Kosher Island'}
{'_id': ObjectId('6749593179a7fce314ff1bbb'), 'borough': 'Brooklyn', 'cuisine': 'Delicatessen', 'name': "Wilken'S Fine Food"}
{'_id': ObjectId('6749593179a7fce314ff1bbc'), 'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Regina Caterers'}
{'_id': ObjectId

In [27]:
#22.Find the restaurant Id, name, borough and cuisine for those restaurants which prepared dish except 'American' and 'Chinese' or restaurant's name begins with letter 'Wil'.
results = collection.find(
    {
        "$or": [
            {"cuisine": {"$nin": ["American", "Chinese"]}},  # Cuisine not 'American' or 'Chinese'
            {"name": {"$regex": "^Wil", "$options": "i"}}   # Name starts with 'Wil'
        ]
    },
    {
        "_id": 1,              # Include restaurant Id
        "name": 1,             # Include restaurant name
        "borough": 1,          # Include borough
        "cuisine": 1           # Include cuisine
    }
)
for doc in results:
    print(doc)

{'_id': ObjectId('6749593179a7fce314ff1bb4'), 'borough': 'Bronx', 'cuisine': 'Bakery', 'name': 'Morris Park Bake Shop'}
{'_id': ObjectId('6749593179a7fce314ff1bb5'), 'borough': 'Brooklyn', 'cuisine': 'Hamburgers', 'name': "Wendy'S"}
{'_id': ObjectId('6749593179a7fce314ff1bb6'), 'borough': 'Manhattan', 'cuisine': 'Irish', 'name': 'Dj Reynolds Pub And Restaurant'}
{'_id': ObjectId('6749593179a7fce314ff1bb7'), 'borough': 'Brooklyn', 'cuisine': 'American ', 'name': 'Riviera Caterer'}
{'_id': ObjectId('6749593179a7fce314ff1bb8'), 'borough': 'Queens', 'cuisine': 'Jewish/Kosher', 'name': 'Tov Kosher Kitchen'}
{'_id': ObjectId('6749593179a7fce314ff1bb9'), 'borough': 'Queens', 'cuisine': 'American ', 'name': 'Brunos On The Boulevard'}
{'_id': ObjectId('6749593179a7fce314ff1bba'), 'borough': 'Staten Island', 'cuisine': 'Jewish/Kosher', 'name': 'Kosher Island'}
{'_id': ObjectId('6749593179a7fce314ff1bbb'), 'borough': 'Brooklyn', 'cuisine': 'Delicatessen', 'name': "Wilken'S Fine Food"}
{'_id': Obj

In [28]:
# 23.Find the restaurant Id, name, and grades for those restaurants which achieved a grade of "A" and scored 11 on an ISODate "2014-08-11T00:00:00Z" among many of survey dates.

target_date = "2014-08-11T00:00:00"
target_score = 11

query = {
    "grades.grade": "A",       
    "grades.score": target_score,
    "grades.date": target_date
}

projection = {"restaurant_id": 1, "name": 1, "grades": 1}
result = collection.find(query, projection)

for restaurant in result:
    print(f"Restaurant ID: {restaurant['restaurant_id']}, Name: {restaurant['name']}")
    for grade in restaurant["grades"]:
        if grade["grade"] == "A" and grade["score"] == target_score and grade["date"] == target_date:
            print(f"  Grade: {grade['grade']}, Score: {grade['score']}, Date: {grade['date']}")

Restaurant ID: 40365871, Name: Neary'S Pub
Restaurant ID: 40372417, Name: Don Filippo Restaurant
  Grade: A, Score: 11, Date: 2014-08-11T00:00:00
Restaurant ID: 40397374, Name: Mustang Sally'S Restaurant
Restaurant ID: 40526406, Name: Club Macanudo (Cigar Bar)
Restaurant ID: 40560917, Name: Marino'S Pizza & Restaurant
Restaurant ID: 40614916, Name: Gene'S Coffee Shop
Restaurant ID: 40698823, Name: Union Cafe Restaurant
Restaurant ID: 40892913, Name: Jojo'S Pizza


In [29]:
# 24.Find the restaurant Id, name and grades for those restaurants where the 2nd element of grades array contains a grade of "A" and score 9 on an ISODate "2014-08-11T00:00:00Z".
target_date = "2014-08-11T00:00:00"
target_score = 9

query = {
    "grades.1.grade": "A",
    "grades.1.score": target_score,
    "grades.1.date": target_date
}

projection = {"restaurant_id": 1, "name": 1, "grades": 1}

result = collection.find(query, projection)

for restaurant in result:
    print(f"Restaurant ID: {restaurant['restaurant_id']}, Name: {restaurant['name']}")
    for grade in restaurant["grades"]:
        if grade["grade"] == "A" and grade["score"] == target_score and grade["date"] == target_date:
            print(f"  Grade: {grade['grade']}, Score: {grade['score']}, Date: {grade['date']}")


Restaurant ID: 40526406, Name: Club Macanudo (Cigar Bar)
  Grade: A, Score: 9, Date: 2014-08-11T00:00:00


In [30]:
# 25.Find the restaurant Id, name, address and geographical location for those restaurants where 2nd element of coordinates contains a value which is more than 42 and up to 52.

query = {
    "address.coord.1": { "$gt": 42, "$lte": 52 }  # Query the second element of coordinates
}

projection = {"restaurant_id": 1, "name": 1, "address": 1, "coordinates": 1}

result = collection.find(query, projection)
for restaurant in result:
    print(f"Restaurant ID: {restaurant['restaurant_id']}, Name: {restaurant['name']}")
    print(f"  Address: {restaurant['address']}")
    print(f"  Geographical Location (Coordinates): {restaurant['address']['coord']}")


Restaurant ID: 40387990, Name: T.G.I. Friday'S
  Address: {'building': '47', 'coord': [-78.877224, 42.89546199999999], 'street': 'Broadway @ Trinity Pl', 'zipcode': '10006'}
  Geographical Location (Coordinates): [-78.877224, 42.89546199999999]
Restaurant ID: 40388936, Name: T.G.I. Fridays
  Address: {'building': '1', 'coord': [-0.7119979, 51.6514664], 'street': 'Pennplaza E, Penn Sta', 'zipcode': '10001'}
  Geographical Location (Coordinates): [-0.7119979, 51.6514664]
Restaurant ID: 40402284, Name: Di Luvio'S Deli
  Address: {'building': '3000', 'coord': [-87.86567699999999, 42.61150920000001], 'street': '47 Avenue', 'zipcode': '11101'}
  Geographical Location (Coordinates): [-87.86567699999999, 42.61150920000001]
Restaurant ID: 40568285, Name: La Caridad 78
  Address: {'building': '21972199', 'coord': [-78.589606, 42.8912372], 'street': 'Broadway', 'zipcode': '10024'}
  Geographical Location (Coordinates): [-78.589606, 42.8912372]
Restaurant ID: 40876618, Name: Bijan'S
  Address: {'b

# Question 2. Restaurant foreclosures in North Carolina – 75 Points

In [31]:
import pandas as pd
import pymongo
import json

client = pymongo.MongoClient("mongodb://localhost:27017/")
db = client["durham_data"]  # Database name
restaurants_collection = db["durham_restaurants"]
foreclosures_collection = db["durham_foreclosures"]

restaurants_file = "Restaurants_in_Durham_County_NC.csv"
restaurants_df = pd.read_csv(
    restaurants_file, 
    delimiter=';', 
    on_bad_lines='skip'
)

restaurants_json = json.loads(restaurants_df.to_json(orient="records"))
restaurants_collection.insert_many(restaurants_json)
print(f"Inserted {len(restaurants_json)} records into 'durham_restaurants' collection.")

foreclosures_file = "durham-nc-foreclosure-2006-2016.json"
with open(foreclosures_file, "r") as f:
    foreclosures_data = json.load(f)

foreclosures_flattened = []
for record in foreclosures_data:
    flat_record = {
        "datasetid": record.get("datasetid"),
        "recordid": record.get("recordid"),
        "record_timestamp": record.get("record_timestamp"),
        **record.get("fields", {}),
        **record.get("geometry", {})
    }
    foreclosures_flattened.append(flat_record)

foreclosures_collection.insert_many(foreclosures_flattened)
print(f"Inserted {len(foreclosures_flattened)} records into 'durham_foreclosures' collection.")


Inserted 2463 records into 'durham_restaurants' collection.
Inserted 1948 records into 'durham_foreclosures' collection.


In [32]:
restaurant_sample = restaurants_collection.find_one()
foreclosure_sample = foreclosures_collection.find_one()

# Print one document from each collection
print("Sample from 'durham_restaurants' collection:")
print(restaurant_sample)

print("\nSample from 'durham_foreclosures' collection:")
print(foreclosure_sample)




Sample from 'durham_restaurants' collection:
{'_id': ObjectId('6749593179a7fce314ff2a71'), 'ID': 56060, 'Premise_Name': 'WEST 94TH ST PUB', 'Premise_Address1': '4711 HOPE VALLEY RD', 'Premise_Address2': 'SUITE 6C', 'Premise_City': 'DURHAM', 'Premise_State': 'NC', 'Premise_Zip': '27707', 'Premise_Phone': '(919) 403-0025', 'Hours_Of_Operation': None, 'Opening_Date': '1994-09-01', 'Closing_Date': None, 'Seats': 60.0, 'Water': '5 - Municipal/Community', 'Sewage': '3 - Municipal/Community', 'Insp_Freq': 4, 'Est_Group_Desc': 'Full-Service Restaurant', 'Risk': 4, 'Smoking_Allowed': 'NO', 'Type_Description': '1 - Restaurant', 'Rpt_Area_Desc': 'Food Service', 'Status': 'ACTIVE', 'Transitional_Type_Desc': 'FOOD', 'geolocation': '35.9207272, -78.9573299'}

Sample from 'durham_foreclosures' collection:
{'_id': ObjectId('6749593179a7fce314ff3410'), 'datasetid': 'foreclosure-2006-2016', 'recordid': '629979c85b1cc68c1d4ee8cc351050bfe3592c62', 'record_timestamp': '2017-03-06T12:41:48-05:00', 'parcel_n

In [33]:
# STEP 1 : FIND ALL DOCUMENTS & COLLECT ALL THE COORDINATES TO FORM A LOGICAL POLYGON

restaurants_in_polygon = restaurants_collection.find({
    "Rpt_Area_Desc": "Food Service",
    "Seats": {"$gte": 100}
})


restaurant_coordinates = []

for restaurant in restaurants_in_polygon:
    geolocation = restaurant.get('geolocation')
    
    if geolocation:
        coords = geolocation.split(', ')
        if len(coords) == 2:
            try:
                lat, lon = float(coords[0]), float(coords[1])
                restaurant_coordinates.append([lon, lat])
            except ValueError:
                continue 

print(restaurant_coordinates)

[[-78.8895483, 36.0467802], [-78.9060312, 36.0183378], [-78.9391734, 36.001517], [-78.9447645, 35.9950533], [-78.9447645, 35.9950533], [-78.9417564, 35.9953688], [-78.8482093, 36.1027227], [-78.964034, 35.955213], [-78.9085238, 36.0732931], [-78.9567106, 36.0262558], [-78.9447416, 36.0199128], [-78.8555425, 35.9261083], [-78.9968077, 35.9533167], [-78.957548, 35.9022771], [-78.9368593, 35.9053183], [-78.897126, 35.8896949], [-78.901896, 35.9973818], [-78.9214948, 36.0292494], [-78.8667135, 35.8703056], [-78.8587915, 35.8919782], [-78.9102149, 36.018111], [-78.9396844, 35.9015132], [-78.9448592, 35.9048455], [-78.9391734, 36.001517], [-78.9447645, 35.9950533], [-78.842243, 35.9183575], [-78.9914286, 35.9533171], [-78.9363925, 35.9125482], [-78.9114595, 36.0765775], [-78.9370134, 35.90396], [-78.9910531, 35.9536413], [-78.9047837, 36.0644085], [-78.9598551, 35.9195187], [-78.960942, 35.9658593], [-78.9217794, 36.0093112], [-78.9046188, 36.0495727], [-78.8108783, 35.9205016], [-78.9462673

In [34]:
# STEP 2 : CREATING A GEOSPATIAL INDEX

foreclosures_collection.create_index([("coordinates", pymongo.GEOSPHERE)])


'coordinates_2dsphere'

In [35]:
# STEP 3 : INSERTING THE RESTAURANT COORDINATES AS A PARAMETER TO THE GEOSPHERE POLYGON QUERY
polygon_query = {
    "coordinates": {
        "$geoWithin": {
            "$polygon": restaurant_coordinates
        }
    }
}

foreclosures_in_polygon = foreclosures_collection.find(polygon_query)

#FORECLOSURES WITHIN IN THE GEOSPHERE POLYGON
foreclosure_count = 0
for foreclosure in foreclosures_in_polygon:
    foreclosure_count+=1
    print(foreclosure)


{'_id': ObjectId('6749593179a7fce314ff3413'), 'datasetid': 'foreclosure-2006-2016', 'recordid': '7ec0761bd385bab8af10f682115a6eb4400740b3', 'record_timestamp': '2017-03-06T12:41:48-05:00', 'parcel_number': '111324', 'geocode': [35.9957683, -78.8873774], 'address': '918 GILBERT ST', 'year': '2006', 'type': 'Point', 'coordinates': [-78.8873774, 35.9957683]}
{'_id': ObjectId('6749593179a7fce314ff3414'), 'datasetid': 'foreclosure-2006-2016', 'recordid': 'c81ae2921ffca8125c2de2fd3e3b1375388cd925', 'record_timestamp': '2017-03-06T12:41:48-05:00', 'parcel_number': '111399', 'geocode': [35.993026, -78.888343], 'address': '721 LIBERTY ST', 'year': '2006', 'type': 'Point', 'coordinates': [-78.888343, 35.993026]}
{'_id': ObjectId('6749593179a7fce314ff3415'), 'datasetid': 'foreclosure-2006-2016', 'recordid': 'ae17ea44c5918fd2db5e54144cc84956c830e009', 'record_timestamp': '2017-03-06T12:41:48-05:00', 'parcel_number': '111426', 'geocode': [35.99217, -78.888092], 'address': '729 HOPKINS ST', 'year': 

In [36]:
print(f"Number of foreclosures within the polygon: {foreclosure_count}")

Number of foreclosures within the polygon: 738


# Question 2 Extension :- Question 7 of HW2 Using Mongo DB

#### I wasnt sure whether I have to do Q7 from HW2 or Q2 from current HW, so I asked professor to do both.

#### This approach uses a geospatial query with MongoDB to approximate a circular search area as a polygon. First, we define a center point (e.g., specific coordinates) and a radius (e.g., 1 mile). A polygon is constructed to approximate the circle by calculating multiple equally spaced points around the center using trigonometric functions. This polygon is then used to query the restaurants and foreclosures collections with the geoWithin operator, identifying all entities that fall within the defined boundary. By leveraging geospatial indexing, the database efficiently retrieves results without manual distance calculations, allowing the same polygon to be reused for multiple queries, such as finding restaurants or counting foreclosures. This approach balances accuracy and performance while simplifying the geospatial search.

In [37]:
import math

target_coordinates = (35.994914, -78.897133)
radius_in_miles = 1  # 1-mile radius

def create_circle_polygon(center, radius, num_points=36):
    """Creates a polygon approximating a circle."""
    lat, lon = center
    earth_radius_miles = 3958.8 
    angular_radius = radius / earth_radius_miles * (180 / math.pi)
    
    polygon = []
    for i in range(num_points):
        angle = 2 * math.pi * i / num_points
        offset_lat = angular_radius * math.cos(angle)
        offset_lon = angular_radius * math.sin(angle) / math.cos(math.radians(lat))
        polygon.append([lon + offset_lon, lat + offset_lat])
    polygon.append(polygon[0])
    return polygon

circle_polygon = create_circle_polygon(target_coordinates, radius_in_miles)
restaurants_within_circle = restaurants_collection.find({
    "Rpt_Area_Desc": "Food Service",
    "Status": "ACTIVE",
    "geolocation": {
        "$geoWithin": {
            "$polygon": circle_polygon
        }
    }
})

closest_restaurant = None
for restaurant in restaurants_within_circle:
    closest_restaurant = restaurant
    print("Closest Restaurant:", closest_restaurant)
    break

foreclosures_within_circle = foreclosures_collection.find({
    "coordinates": {
        "$geoWithin": {
            "$polygon": circle_polygon
        }
    }
})

foreclosure_count = 0
for foreclosure in foreclosures_within_circle:
    foreclosure_count += 1

print("Foreclosure Count within 1 mile:", foreclosure_count)

Foreclosure Count within 1 mile: 289


# Question 3 : Extra Credit: 40 points

In [38]:
import pandas as pd
import json

worldcities_df = pd.read_csv('worldcities.csv')
print("World Cities Schema:")
print(worldcities_df.info())

meteorites_data = []
with open('meteorites.json', 'r') as file:
    for line in file:
        meteorites_data.append(json.loads(line.strip()))

meteorites_df = pd.json_normalize(meteorites_data)
print("Meteorites Schema:")
print(meteorites_df.info())


World Cities Schema:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12893 entries, 0 to 12892
Data columns (total 11 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   city        12893 non-null  object 
 1   city_ascii  12893 non-null  object 
 2   lat         12893 non-null  float64
 3   lng         12893 non-null  float64
 4   country     12893 non-null  object 
 5   iso2        12862 non-null  object 
 6   iso3        12893 non-null  object 
 7   admin_name  12721 non-null  object 
 8   capital     5063 non-null   object 
 9   population  11276 non-null  float64
 10  id          12893 non-null  int64  
dtypes: float64(3), int64(1), object(7)
memory usage: 1.1+ MB
None
Meteorites Schema:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 13 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   fall                      

In [39]:
# INSERTING INTO THE DATABASE.

client = MongoClient('mongodb://localhost:27017/')

worldcities_db = client['worldcities_db']
meteorites_db = client['meteorites_db']

worldcities_collection = worldcities_db['cities']
worldcities_collection.insert_many(worldcities_df.to_dict('records'))

meteorites_collection = meteorites_db['meteorites']
meteorites_collection.insert_many(meteorites_df.to_dict('records'))

print("Data successfully inserted into MongoDB!")
print(f"Number of records in worldcities collection: {worldcities_collection.count_documents({})}")
print(f"Number of records in meteorites collection: {meteorites_collection.count_documents({})}")

Data successfully inserted into MongoDB!
Number of records in worldcities collection: 12893
Number of records in meteorites collection: 1000


In [40]:
# CLEANING THE JSON AND REORDERING THE COORDINATES

for city in worldcities_collection.find():
    if city.get("lat") is not None and city.get("lng") is not None:
        coordinates = [city["lng"], city["lat"]]  # [longitude, latitude]
        
        worldcities_collection.update_one(
            {"_id": city["_id"]},
            {"$set": {
                "coordinates": coordinates
            }}
        )


In [41]:
worldcities_collection.create_index([("coordinates", "2dsphere")])


'coordinates_2dsphere'

In [42]:
#TESTING ONE CITY 

meteorite_coordinates = [6.08333, 50.775] 
closest_city = worldcities_collection.find_one({
    "coordinates": {
        "$near": {
            "$geometry": {
                "type": "Point",
                "coordinates": meteorite_coordinates
            }
        }
    }
})

if closest_city:
    print(f"Closest City: {closest_city['city']}")
else:
    print("No closest city found")


Closest City: Maastricht


In [43]:
#Here I AM Manually extracting the meteorite_coordinates into a separate array just to avoid any confusion for my own self, 
# we can direclty use the meteorite coordinate values as input into the geosphere index, but this is just for my ease
# in reading...

meteorite_coordinates_list = []

for meteorite in meteorites_collection.find():
    if "geolocation.coordinates" in meteorite:
        meteorite_coordinates = meteorite["geolocation.coordinates"]
        if meteorite_coordinates: 
            meteorite_coordinates_list.append(meteorite_coordinates)

print(meteorite_coordinates_list)


[[6.08333, 50.775], [10.23333, 56.18333], [-113, 54.21667], [-99.9, 16.88333], [-64.95, -33.16667], [71.8, 32.1], [95.16667, 44.83333], [0.61667, 44.21667], [-65.23333, -31.6], [-64.55, -30.86667], [-9.57028, 16.39806], [8.38333, 19.08333], [2.33333, 50.66667], [35.05, 29.51667], [77.95, 29.71667], [8.43333, 8.91667], [42.81667, 39.91667], [39.51667, 24.41667], [28.96, 13.66033], [4.08333, 44.11667], [11.01667, 44.65], [22.66667, 2], [6.01533, 45.82133], [-1.78333, 51.78333], [37.13333, 36.23333], [8.75, 44.88333], [31.81667, 50.95], [10.15, 45.26667], [-85.88333, 42.53333], [-105.31667, 26.96667], [32.41275, 20.74575], [44.21556, 35.27333], [78.25, 27.66667], [85.56667, 26.58333], [-70.75, 44.61667], [37.5, 48.7], [76.86667, 20.88333], [0, 0], [-0.55, 47.46667], [-44.31667, -22.96667], [39.71667, 9.53333], [105.18333, 25.15], [140.78556, 40.81056], [-2.71667, 53.58333], [5.38333, 43.86667], [-66, -33], [-94.3, 38.5], [-60.66667, -31.41667], [9.03333, 42.45], [-97.01, 31.805], [0.3, 52

In [44]:
# I AM USING $near operator of MongoDB

import math

for meteorite_coordinates in meteorite_coordinates_list:
    if isinstance(meteorite_coordinates, list):
        if any(map(math.isnan, meteorite_coordinates)): 
            print(f"Skipping meteorite with invalid coordinates: {meteorite_coordinates}")
            continue
    elif math.isnan(meteorite_coordinates):
        print(f"Skipping meteorite with invalid coordinates: {meteorite_coordinates}")
        continue

    print(f"Searching for closest city to meteorite with coordinates {meteorite_coordinates}")

    closest_city = worldcities_collection.find_one({
        "coordinates": {
            "$near": {
                "$geometry": {
                    "type": "Point",
                    "coordinates": meteorite_coordinates
                }
            }
        }
    })

    if closest_city:
        print(f"Closest City: {closest_city['city']}")
    else:
        print("No closest city found")



Searching for closest city to meteorite with coordinates [6.08333, 50.775]
Closest City: Maastricht
Searching for closest city to meteorite with coordinates [10.23333, 56.18333]
Closest City: Århus
Searching for closest city to meteorite with coordinates [-113, 54.21667]
Closest City: Athabasca
Searching for closest city to meteorite with coordinates [-99.9, 16.88333]
Closest City: Acapulco
Searching for closest city to meteorite with coordinates [-64.95, -33.16667]
Closest City: Río Cuarto
Searching for closest city to meteorite with coordinates [71.8, 32.1]
Closest City: Kundian
Searching for closest city to meteorite with coordinates [95.16667, 44.83333]
Closest City: Altay
Searching for closest city to meteorite with coordinates [0.61667, 44.21667]
Closest City: Agen
Searching for closest city to meteorite with coordinates [-65.23333, -31.6]
Closest City: Villa Carlos Paz
Searching for closest city to meteorite with coordinates [-64.55, -30.86667]
Closest City: Villa Carlos Paz
Sea

# Q0: Load all datasets into MongoDB. Prove it. – 25 Points

##### SCRIPT TO PRINT ONE DOCUMENT FROM EACH DB, TOTAL # OF DOCUMENTS & TOTAL # of Collections AS PROOF OF DATA LOADING 

In [45]:
databases = [db for db in client.list_database_names() if db not in ['admin', 'config', 'local']]

for db_name in databases:
    db = client[db_name]
    collections = db.list_collection_names()
    print(f"Database: {db_name}")
    print(f"Total Collections: {len(collections)}")
    for collection_name in collections:
        collection = db[collection_name]
        document_count = collection.count_documents({})
        print(f"Collection: {collection_name}")
        print(f"Number of Documents: {document_count}")
        document = collection.find_one()
        print(document)
        print("\n" + "="*50 + "\n")


Database: durham_data
Total Collections: 2
Collection: durham_restaurants
Number of Documents: 2463
{'_id': ObjectId('6749593179a7fce314ff2a71'), 'ID': 56060, 'Premise_Name': 'WEST 94TH ST PUB', 'Premise_Address1': '4711 HOPE VALLEY RD', 'Premise_Address2': 'SUITE 6C', 'Premise_City': 'DURHAM', 'Premise_State': 'NC', 'Premise_Zip': '27707', 'Premise_Phone': '(919) 403-0025', 'Hours_Of_Operation': None, 'Opening_Date': '1994-09-01', 'Closing_Date': None, 'Seats': 60.0, 'Water': '5 - Municipal/Community', 'Sewage': '3 - Municipal/Community', 'Insp_Freq': 4, 'Est_Group_Desc': 'Full-Service Restaurant', 'Risk': 4, 'Smoking_Allowed': 'NO', 'Type_Description': '1 - Restaurant', 'Rpt_Area_Desc': 'Food Service', 'Status': 'ACTIVE', 'Transitional_Type_Desc': 'FOOD', 'geolocation': '35.9207272, -78.9573299'}


Collection: durham_foreclosures
Number of Documents: 1948
{'_id': ObjectId('6749593179a7fce314ff3410'), 'datasetid': 'foreclosure-2006-2016', 'recordid': '629979c85b1cc68c1d4ee8cc351050bfe